# Welcome to PYNQ Audio
This notebook shows the basic recording and playback features of the PYNQ-Z2.  
It uses the audio jack `HP+MIC` to play back recordings; it can take inputs from 
the microphone on `HP+MIC` or `LINE_IN`. Pre-recorded audio sample can also be taken
as input. Moreover, visualization with matplotlib is shown.
## Create new audio object

In [1]:
from pynq.overlays.base import BaseOverlay
import numpy as np
base = BaseOverlay("base.bit")

In [2]:
pAudio = base.audio

## Bypass audio
Users can select either `LINE_IN`, or `HP+MIC` as the input port.
In the following example, we choose `LINE_IN`. To choose `MIC`:
```python
pAudio.select_microphone()
```
or choose `LINE_IN`:
```python
pAudio.select_line_in()
```

In [3]:
pAudio.select_microphone()

## Record and play
Record a 5-second sample and save it into a file.

In [4]:
pAudio.record(5)
pAudio.save("recording_0.wav")

In [5]:
pAudio.record(5)
pAudio.save("recording_1.wav")

## Load and play
Load a sample and play the loaded sample.

In [9]:
pAudio.load("/home/xilinx/jupyter_notebooks/final_project/recording_0.wav")
print(pAudio.info("./recording_0.wav"))
print(pAudio.sample_rate)
x = pAudio.buffer
pAudio.play()

File name:          ./recording_3.wav
Number of channels: 2
Sample width:       3
Sample rate:        48000
Number of frames:   240000
Compression type:   NONE
Compression name:   not compressed
None
48000


AttributeError: 'numpy.ndarray' object has no attribute 'type'

In [10]:
pAudio.load("/home/xilinx/jupyter_notebooks/final_project/recording_1.wav")
print(pAudio.info("./recording_1.wav"))
print(pAudio.sample_rate)
y = pAudio.buffer
pAudio.play()

File name:          ./recording_0.wav
Number of channels: 2
Sample width:       3
Sample rate:        48000
Number of frames:   240000
Compression type:   NONE
Compression name:   not compressed
None
48000


## 實作音源串接

In [28]:
import wave
import audioop
z = x + y
with wave.open("./recording_0.wav", 'r') as wav_file:
    num_frames = wav_file.getnframes()
    raw_frames = wav_file.readframes(num_frames)
    num_channels = wav_file.getnchannels()
    sample_rate = wav_file.getframerate()
    sample_width = wav_file.getsampwidth()
    comptype = wav_file.getcomptype()
    compname = wav_file.getcompname()
with wave.open("./recording_1.wav", 'r') as wav_file:
    num_frames_3 = wav_file.getnframes()
    raw_frames_3 = wav_file.readframes(num_frames)
    num_channels_3 = wav_file.getnchannels()
    sample_rate_3 = wav_file.getframerate()
    sample_width_3 = wav_file.getsampwidth()
    comptype_3 = wav_file.getcomptype()
    compname_3 = wav_file.getcompname()
frames_4 = raw_frames + raw_frames_3
with wave.open("./recording_2.wav", 'w') as wav_write:
    wav_write.setnchannels(num_channels)
    wav_write.setsampwidth(sample_width)
    wav_write.setframerate(sample_rate)
    wav_write.setnframes(num_frames)
    wav_write.setcomptype(comptype,compname)
    wav_write.writeframes(frames_4)

In [29]:
from IPython.display import Audio as IPAudio
IPAudio("./recording_2.wav")

## 將Bitstream File 燒錄至板子上

In [39]:
from pynq import Overlay
Lab_Design = Overlay("./final_project.bit")

/usr/local/lib/python3.6/dist-packages/pynq/overlay.py:299: UserWarning: Users will not get PARAMETERS / REGISTERS information through TCL files. HWH file is recommended.
  warnings.warn(message, UserWarning)


## 從硬體檔案中讀取這個系統中的 AXI ADDRESS

In [40]:
Lab_Design.ip_dict

{'DSP_AXI_wrapper_0': {'addr_range': 65536,
  'driver': pynq.overlay.DefaultIP,
  'fullpath': 'DSP_AXI_wrapper_0',
  'gpio': {},
  'interrupts': {},
  'mem_id': 'SEG_DSP_AXI_wrapper_0_S00_AXI_reg',
  'phys_addr': 1136656384,
  'state': None,
  'type': 'xilinx.com:user:DSP_AXI_wrapper:1.0'}}

## 取出 DSP_AXI 這個 AXI IP 的 Base Address 以及 Address Range
### 可以檢查這個地址是否和Vivado中 `Address Editor` 內 DSP_AXI 的 Base Address 相同

In [41]:
audio_dsp = Lab_Design.ip_dict['DSP_AXI_wrapper_0']['phys_addr']
audio_dsp_range = Lab_Design.ip_dict['DSP_AXI_wrapper_0']['addr_range']
print("The Base Address of convolution is : " + format(audio_dsp, '02x'))
print("The Address Range of convolution is : " + format(audio_dsp_range, '02x'))

The Base Address of convolution is : 43c00000
The Address Range of convolution is : 10000


## 使用Pynq 內建的 MMIO 以達成 PS 和 AXI IP 之間的溝通
### MMIO(IP_BASE_ADDRESS, ADDRESS_RANGE)

In [49]:
from pynq import MMIO
dsp = MMIO(audio_dsp, audio_dsp_range)

## 改變聲音的大小
### 輸入你想要調變的音量大小

In [50]:
volume = 20 #此為原始值
control = 0 #輸入0為增加音量，輸入1為減少音量
mul = 60 #輸入想增加或減少的音量大小

## 將資料寫入並讀取

In [51]:
dsp.write(0x0, mul)
dsp.write(0x4, 1)
dsp.write(0x8, volume)
dsp.write(0xC, control)
output_tmp = dsp.read(0x0)
if output_tmp < 0:
    output=((-1)*((output-1)^(0XFFFFFFFF)))*2
else:
    output = output_tmp * 2
print("The volume you want is: ", output)

The volume you want is:  80


## 實作改變音量大小

In [52]:
import wave
import audioop


wav_path = "./recording_0.wav"
wav_path_1 = "./recording_3.wav"

with wave.open(wav_path, 'r') as wav_file:
    num_frames = wav_file.getnframes()
    raw_frames = wav_file.readframes(num_frames)
    num_channels = wav_file.getnchannels()
    sample_rate = wav_file.getframerate()
    sample_width = wav_file.getsampwidth()
    comptype = wav_file.getcomptype()
    compname = wav_file.getcompname()
mul_data = output/20
print(mul_data)
frames_1 = audioop.mul(raw_frames, sample_width, int(mul_data))


with wave.open(wav_path_1, 'w') as wav_write:
    wav_write.setnchannels(num_channels)
    wav_write.setsampwidth(sample_width)
    wav_write.setframerate(sample_rate)
    wav_write.setnframes(num_frames)
    wav_write.setcomptype(comptype,compname)
    wav_write.writeframes(frames_1)
wav_write.close()

4.0


In [53]:
from IPython.display import Audio as IPAudio
IPAudio("./recording_3.wav")

## 改變聲音的頻率
### 輸入想要變的高頻還是低頻

In [54]:
freq = 1.25 #輸入想要調變的頻率倍率，範圍約為0.5~1.5

## 將資料寫入並讀取

In [55]:
x = freq*100
dsp.write(0x0, int(x))
dsp.write(0x4, 2)
dsp.write(0x8, 0)
dsp.write(0xC, 0)
output_freq = dsp.read(0x0)
print("The frequency you want is: ", output_freq/100)

The frequency you want is:  1.25


## 實作改變頻率

In [59]:
import wave
import audioop


wav_path = "./recording_0.wav"
wav_path_2 = "./recording_4.wav"

with wave.open(wav_path, 'r') as wav_file:
    num_frames = wav_file.getnframes()
    raw_frames = wav_file.readframes(num_frames)
    num_channels = wav_file.getnchannels()
    sample_rate = wav_file.getframerate()
    sample_width = wav_file.getsampwidth()
    comptype = wav_file.getcomptype()
    compname = wav_file.getcompname()

mul_freq = output_freq/100
print(mul_freq)


with wave.open(wav_path_2, 'w') as wav_write:
    wav_write.setnchannels(num_channels)
    wav_write.setsampwidth(sample_width)
    wav_write.setframerate(sample_rate*mul_freq)
    wav_write.setnframes(num_frames)
    wav_write.setcomptype(comptype,compname)
    wav_write.writeframes(raw_frames)

1.25


In [30]:
from IPython.display import Audio as IPAudio
IPAudio("./recording_4.wav")